# Overview

This notebook is meant to demonstrate working with SUPER datatype in Redshift.

We will demonstrate the following features of SUPER datatype
- Support for up to 16MB of data for an individual SUPER field or object
- Loading Semistructured Data
- Querying Semistructured data
- Operators and Functions
- SUPER Configurations

# Set Up Test Data

We will use the modified and nested TPC-H dataset for this demo. Create the required tables for TPC-H dataset using the DDLs below

## Create a demo schema

In [0]:
CREATE SCHEMA super_demo;

## Create tables for test data

In [0]:
CREATE TABLE super_demo.customer_orders_lineitem
(c_custkey bigint
,c_name varchar
,c_address varchar
,c_nationkey smallint
,c_phone varchar
,c_acctbal decimal(12,2)
,c_mktsegment varchar
,c_comment varchar
,c_orders super
);

/*

Datamodel of documents to be stored in c_orders Super column would be as follows

ARRAY < STRUCT < o_orderkey:bigint
                           ,o_orderstatus:string
                           ,o_totalprice:double
                           ,o_orderdate:string
                           ,o_orderpriority:string
                           ,o_clerk:string
                           ,o_shippriority:int
                           ,o_comment:string
                           ,o_lineitems:ARRAY < STRUCT < l_partkey:bigint
                                                         ,l_suppkey:bigint
                                                         ,l_linenumber:int
                                                         ,l_quantity:double
                                                         ,l_extendedprice:double
                                                         ,l_discount:double
                                                         ,l_tax:double
                                                         ,l_returnflag:string
                                                         ,l_linestatus:string
                                                         ,l_shipdate:string
                                                         ,l_commitdate:string
                                                         ,l_receiptdate:string
                                                         ,l_shipinstruct:string
                                                         ,l_shipmode:string
                                                         ,l_comment:string
                                                         >>
                            >>
*/

CREATE TABLE super_demo.part
(
 p_partkey bigint
 ,p_name varchar
 ,p_mfgr varchar
 ,p_brand varchar
 ,p_type varchar
 ,p_size int
 ,p_container varchar
 ,p_retailprice decimal(12,2)
 ,p_comment varchar
 );

 CREATE TABLE super_demo.supplier_partsupp
(
 s_suppkey bigint
 ,s_name varchar
 ,s_address varchar
 ,s_nationkey smallint
 ,s_phone varchar
 ,s_acctbal double precision
 ,s_comment varchar
 ,s_partsupps super
 );

/*
 Datamodel of documents to be stored in s_partsupps Super column would be as follows
 ARRAY <STRUCT < ps_partkey:bigint,ps_availqty:int,ps_supplycost:double,ps_comment:string >>
*/

 CREATE TABLE super_demo.region_nations
(
 r_regionkey smallint
 ,r_name varchar
 ,r_comment varchar
 ,r_nations super
 );

 /*Datamodel of documents to be stored in r_nations Super column would be as follows
ARRAY < STRUCT < n_nationkey:int,n_name:string,n_comment:string
*/

## Load the test data
Load the test data using the following COPY commands. 

Please ensure you associate an IAM role to cluster as default role and it has S3 full access.

In [0]:
COPY super_demo.customer_orders_lineitem FROM 's3://redshift-downloads/semistructured/tpch-nested/data/json/customer_orders_lineitem' 
REGION 'us-east-1' IAM_ROLE default 
FORMAT JSON 'auto';

COPY super_demo.part FROM 's3://redshift-downloads/semistructured/tpch-nested/data/json/part' 
REGION 'us-east-1' IAM_ROLE default
FORMAT JSON 'auto';

COPY super_demo.supplier_partsupp FROM 's3://redshift-downloads/semistructured/tpch-nested/data/json/supplier_partsupp' 
REGION 'us-east-1' IAM_ROLE default
FORMAT JSON 'auto';

# Features

## Support for up to 16MB of data for an individual SUPER field or object

The SUPER data type supports up to 16 MB of data for an individual SUPER field or object. To demonstrate this feature, we have extrapolated the existing data in the c_orders field for customer_orders_lineitem table and create SUPER objects up to 16 MB. 

We will use the size function to check the size of data stored in c_orders to validate the support for up to 16 MB for SUPER data type

Run the SQL scripts below to validate this feature

In [0]:
-- Create a copy of customer_orders_lineitem table 

CREATE TABLE super_demo.customer_orders_lineitem_16MB
(c_custkey bigint
,c_name varchar
,c_address varchar
,c_nationkey smallint
,c_phone varchar
,c_acctbal decimal(12,2)
,c_mktsegment varchar
,c_comment varchar
,c_orders super
);

-- Copy extrapolated dataset using the script below 

COPY super_demo.customer_orders_lineitem_16MB FROM 's3://redshift-demos/data/superdemo/super_16_data.csv' 
REGION 'us-east-1' IAM_ROLE default
CSV
IGNOREHEADER 1

--Validate using size FUNCTION
Select max(size(c_orders))
from super_demo.customer_orders_lineitem_16MB

## Loading Semistructured Data

To load Semistructured data into Redshift's SUPER data type, you can either use a COPY command or INSERT or UPDATE statements. 

Following section demonstrates how to use both of these methods to load Semistructured data in Amazon Redshift.

### Using COPY command to load the Semistructured data

You can ingest the JSON document using COPY into either a single SUPER data column or multiple Redshift columns. You can use these options with JSON or AVRO formats. 

You can insert or update JSON data into a SUPER column using the json_parse function. The function parses data in JSON format and converts it into the SUPER data type, which you can use in INSERT or UPDATE statements.

The following example inserts JSON data into a SUPER column.

#### Copy from JSON and AVRO

In [0]:
/* COPY of JSON into a single SUPER column */

CREATE TABLE super_demo.region_nations_noshred (rdata SUPER);

/* Replace IAM role */
COPY super_demo.region_nations_noshred FROM 's3://redshift-downloads/semistructured/tpch-nested/data/json/region_nation' 
REGION 'us-east-1' IAM_ROLE DEFAULT 
FORMAT JSON 'noshred';


SELECT rdata FROM super_demo.region_nations_noshred;

/* COPY of JSON into multiple columns */

/* Ingest region_nations, Replace IAM role */

COPY super_demo.region_nations FROM 's3://redshift-downloads/semistructured/tpch-nested/data/json/region_nation' 
REGION 'us-east-1' IAM_ROLE DEFAULT
FORMAT JSON 'auto';

SELECT * FROM super_demo.region_nations limit 1;

#### Copy from columnar formats PARQUET and ORC

In [0]:
--PARQUET
COPY super_demo.region_nations
FROM 's3://redshift-downloads/semistructured/tpch-nested/data/parquet/region_nation'
REGION 'us-east-1' IAM_ROLE DEFAULT
FORMAT PARQUET SERIALIZETOJSON;

--ORC
COPY super_demo.region_nations
FROM 's3://redshift-downloads/semistructured/tpch-nested/data/orc/region_nation'
REGION 'us-east-1' IAM_ROLE DEFAULT
FORMAT ORC SERIALIZETOJSON;

For more examples on how to copy data from other file formats such as text, comma-separated value (CSV) format, please refer the examples [here](https://docs.aws.amazon.com/redshift/latest/dg/ingest-super.html)

### Using Insert to load the Semistructured data

In [0]:
--Parsing of JSON documents and Inserts/Updates to SUPER columns 

INSERT INTO super_demo.region_nations VALUES(0, 
   'lar deposits. blithely final packages cajole. regular waters are final requests. regular accounts are according to',
   'AFRICA',   
   JSON_PARSE('{
   "r_nations":[
      {
         "n_comment":" haggle. carefully final deposits detect slyly agai",
         "n_nationkey":0,
         "n_name":"ALGERIA"
      },
      {
         "n_comment":"ven packages wake quickly. regu",
         "n_nationkey":5,
         "n_name":"ETHIOPIA"
      },
      {
         "n_comment":" pending excuses haggle furiously deposits. pending, express pinto beans wake fluffily past t",
         "n_nationkey":14,
         "n_name":"KENYA"
      },
      {
         "n_comment":"rns. blithely bold courts among the closely regular packages use furiously bold platelets?",
         "n_nationkey":15,
         "n_name":"MOROCCO"
      },
      {
         "n_comment":"s. ironic, unusual asymptotes wake blithely r",
         "n_nationkey":16,
         "n_name":"MOZAMBIQUE"
      }
   ]
}'));

## Querying Semistructured Data

### Navigation

Amazon Redshift uses [PartiQL](https://docs.aws.amazon.com/amazondynamodb/latest/developerguide/ql-reference.html) to enable navigation into arrays and structures using the [...] bracket and dot notation respectively. You can use the dot and bracket notations in all types of queries, such as filtering, join, and aggregation. You can use these notations in a query in which there are normally column references. Please see the following examples.

In [0]:
--The following example uses a SELECT statement that filters results

SELECT count(*) FROM super_demo.customer_orders_lineitem WHERE c_orders[0]. o_orderkey IS NOT NULL;

--The following example uses the bracket and dot navigation in both GROUP BY and ORDER BY clauses.

SELECT c_orders[0].o_orderdate,
       c_orders[0].o_orderstatus,
       count(*)
FROM super_demo.customer_orders_lineitem
WHERE c_orders[0].o_orderkey IS NOT NULL
GROUP BY c_orders[0].o_orderstatus,
         c_orders[0].o_orderdate
ORDER BY c_orders[0].o_orderdate;

### Unnesting

Amazon Redshift uses PartiQL syntax to iterate over SUPER arrays. It does this by navigating the array using the FROM clause of a query. 
he PartiQL syntax of unnesting using the FROM clause item x (AS) y means that y iterates over each (SUPER) value in (SUPER) array expression x. In this case, x is a SUPER expression and y is an alias for x. 

 In the below example, customer_orders_lineitem c is the iteration over the customer_order_lineitem base table and c.c_orders o is the iteration over the c.c_orders array

In [0]:
SELECT c.*, o FROM super_demo.customer_orders_lineitem c, c.c_orders o;

Amazon Redshift also supports an array index when iterating over the array using the AT keyword. The clause x AS y AT z iterates over array x and generates the field z, which is the array index. The following example shows how an array index works.

In [0]:
SELECT c_name,
       orders.o_orderkey AS orderkey,
       index AS orderkey_index
FROM super_demo.customer_orders_lineitem c, c.c_orders AS orders AT index 
ORDER BY orderkey_index;

### Unpivoting

To perform object unpivoting, Amazon Redshift uses the PartiQL syntax to iterate over SUPER objects. It does this using the FROM clause of a query with the UNPIVOT keyword. The following query iterates over the c.c_orders[0] object.

In [0]:
SELECT attr as attribute_name, json_typeof(val) as value_type 
FROM super_demo.customer_orders_lineitem c, UNPIVOT c.c_orders[0] AS val AT attr 
WHERE c_custkey = 9451;

As with unnesting, the unpivoting syntax is also an extension of the FROM clause. The difference is that the unpivoting syntax uses the UNPIVOT keyword to indicate that it's iterating over an object instead of an array. It uses the AS value_alias for iteration over all the values inside an object and uses the AT attribute_alias for iterating over all the attributes.

Amazon Redshift also supports using object unpivoting and array unnesting in a single FROM clause as follows.

In [0]:
SELECT attr as attribute_name, val as object_value
FROM super_demo.customer_orders_lineitem c, c.c_orders AS o, UNPIVOT o AS val AT attr 
WHERE c_custkey = 9451;

## Operations and Functions

Amazon Redshift provides the following function support of SUPER operations and Functions:
- Arithmetics operators
- Arithmetic Functions
- Array Functions

### Arithmetic operators

SUPER values support all basic arithmetic operators +, -, *, /, %. The resultant type of the operation remains as SUPER. For all operators, except for the binary operator +, the input operands must be numbers. Otherwise, Amazon Redshift returns null. Please see the following example

In [0]:
SELECT (c_orders[0]. o_orderkey + 0.5) * c_orders[0]. o_orderkey / 10 AS math FROM super_demo.customer_orders_lineitem;

### Arithmetic Functions

Amazon Redshift supports the following arithmetic functions for SUPER columns. They return null if the input isn't a number:

- FLOOR. For more information, see [FLOOR function](https://docs.aws.amazon.com/redshift/latest/dg/r_FLOOR.html).

- CEIL and CEILING. For more information, see [CEILING (or CEIL) function](https://docs.aws.amazon.com/redshift/latest/dg/r_CEILING_FLOOR.html).

- ROUND. For more information, see [ROUND function](https://docs.aws.amazon.com/redshift/latest/dg/r_ROUND.html).

- TRUNC. For more information, see [TRUNC function](https://docs.aws.amazon.com/redshift/latest/dg/r_TRUNC.html).

- ABS. For more information, see [ABS function](https://docs.aws.amazon.com/redshift/latest/dg/r_ABS.html).

The following example uses arithmetic functions to query data:

In [0]:
SELECT x, FLOOR(x), CEIL(x), ROUND(x)
FROM (
    SELECT (c_orders[0]. o_orderkey + 0.5) * c_orders[0].o_orderkey / 10 AS x
    FROM super_demo.customer_orders_lineitem
    );

### Array Functions

Amazon Redshift supports the following array composition and utility functions array, array_concat, subarray, array_flatten, get_array_length, and split_to_array.

Following examples show how each of these functions can be used.

You can construct SUPER arrays from values in Amazon Redshift data types using the ARRAY function, including other SUPER values. The following example uses the variadic function ARRAY:

In [0]:
SELECT ARRAY(1, c.c_custkey, NULL, c.c_name, 'abc') FROM super_demo.customer_orders_lineitem c;

The following example uses array concatenation with the ARRAY_CONCAT function:

In [0]:
SELECT ARRAY_CONCAT(JSON_PARSE('[10001,10002]'),JSON_PARSE('[10003,10004]'));

The following example uses array manipulation with the SUBARRAY function which returns a subset of the input array.

In [0]:
SELECT SUBARRAY(ARRAY('a', 'b', 'c', 'd', 'e', 'f'), 2, 3);

The following example merges multiple levels of arrays into a single array using ARRAY_FLATTEN:

In [0]:
SELECT x, ARRAY_FLATTEN(x) FROM (SELECT ARRAY(1, ARRAY(2, ARRAY(3, ARRAY()))) AS x);

The GET_ARRAY_LENGTH function returns the length of a SUPER array given an object or array path.

In [0]:
SELECT c_name
FROM super_demo.customer_orders_lineitem
WHERE GET_ARRAY_LENGTH(c_orders) = (
    SELECT MAX(GET_ARRAY_LENGTH(c_orders))
    FROM super_demo.customer_orders_lineitem
    );

The following example splits a string to an array of strings using SPLIT_TO_ARRAY. The function uses a delimiter as an optional parameter. If no delimiter is absent, then the default is a comma.

In [0]:
SELECT SPLIT_TO_ARRAY('12|345|6789', '|');

## Super Configurations

Note the following considerations of SUPER configurations when you use Amazon Redshift SUPER data type and PartiQL.
- Lax and Strict modes for SUPER
- Accessing JSON fields with uppercase and mixedcase field names or attributes
- Parsing options for SUPER

### Lax and strict modes for SUPER

When you query SUPER data, the path expression may not match the actual SUPER data structure. If you try to access a non-existent member of an object or element of an array, Amazon Redshift returns a NULL value if your query is run in the default lax mode. If you run your query in the strict mode, Amazon Redshift returns an error. The following session parameters can be set to set the lax mode on or off.

The following example uses session parameters to enable lax mode.

In [0]:
SET navigate_super_null_on_error=ON;  --default lax mode for navigation

SET cast_super_null_on_error=ON;  --default lax mode for casting

SET parse_super_null_on_error=OFF;  --default strict mode for ingestion

### Accessing JSON fields with uppercase and mixedcase field names or attributes

When your JSON attribute names are in uppercase or mixedcase, you must be able to navigate SUPER type structures in a case sensitive way. To do that, you can configure enable_case_sensitive_identifier to TRUE and wrap the uppercase and mixedcase attribute names with double quotation marks. 
The following example illustrates how to set enable_case_sensitive_identifier to query data.

In [0]:
SET enable_case_sensitive_identifier to TRUE;
 
-- Accessing JSON attribute names with uppercase and mixedcase names
SELECT json_table.data."ITEMS"."Name",
       json_table.data."price"
FROM
  (SELECT json_parse('{"ITEMS":{"Name":"TV"}, "price": 345}') AS data) AS json_table;

In [0]:
RESET enable_case_sensitive_identifier;
 
-- After resetting the above configuration, the following query accessing JSON attribute names with uppercase and mixedcase names should return null (if in lax mode).
SELECT json_table.data."ITEMS"."Name",
       json_table.data."price"
FROM
  (SELECT json_parse('{"ITEMS":{"Name":"TV"}, "price": 345}') AS data) AS json_table;

You can also configure enable_case_sensitive_super_attribute to TRUE. In this case, you can use uppercase and mixedcase attribute names in your queries without wrapping them in double quotation marks.

The following example illustrates how to set enable_case_sensitive_super_attribute to query data.

In [0]:
SET enable_case_sensitive_super_attribute to TRUE;
 -- Accessing JSON attribute names with uppercase and mixedcase names
 
SELECT json_table.data.ITEMS.Name,
       json_table.data.price 
FROM
  (SELECT json_parse('{"ITEMS":{"Name":"TV"}, "price": 345}') AS data) AS json_table;

In [0]:
RESET enable_case_sensitive_super_attribute;
 
 -- After resetting enable_case_sensitive_super_attribute, the query now returns NULL for ITEMS.Name (if in lax mode).
 
SELECT json_table.data.ITEMS.Name,
       json_table.data.price 
FROM
  (SELECT json_parse('{"ITEMS":{"Name":"TV"}, "price": 345}') AS data) AS json_table;

### Parsing options for SUPER

When you use the JSON_PARSE function to parse JSON strings into SUPER values, certain restrictions apply:

- The same attribute name cannot appear in the same object, but can appear in a nested object. The json_parse_dedup_attributes configuration option allows JSON_PARSE to keep only the last occurrence of duplicate attributes instead of returning an error.

- String values cannot exceed the system max varchar size of 65535 bytes. The json_parse_truncate_strings configuration option allows JSON_PARSE() to automatically truncate strings that are longer than this limit without returning an error. This behavior affects string values only and not attribute names.

The following example shows how to set the json_parse_dedup_attributes configuration option to the default behavior of returning an error for duplicate attributes.

In [0]:
SET json_parse_dedup_attributes=OFF;  --default behavior of returning error instead of de-duplicating attributes

The following example shows how to set the json_parse_truncate_strings configuration option for the default behavior of returning an error for strings that are longer than this limit.

In [0]:
SET json_parse_truncate_strings=OFF;  --default behavior of returning error instead of truncating strings

# Clean Up

Drop the super_demo schema

In [0]:
DROP SCHEMA CASCADE;